# CSNMR-3198_sanity_check
# Notes

## 0715-0717:
- BX2GEO/ seems to be missing Antenna #2 (No SNR values in record 35:19 for 2nd antenna)
- 6303C55359/6303C55359202407172100.T04 seems to be corrupt. (last file) The rest of the files in that dir seem OK.
- 6348C01926/ Seems ok

## 0717-0722:
- BXGEO/ seems to be missing Antenna #2 (No SNR values in record 35:19 for 2nd antenna)
- BXGEO/BXGEO_____202407221300.T04 is corrupt (last file)
- 6303C55359202407221300.T04 is corrupt (last file)
- 6348C01926/6348C01926202407172200.T04 is corrupt (first file)
- 6348C01926/6348C01926202407221300.T04 is corrup (last file)

The corrupted files were deleted prior to running `viewdat`

# Imports

In [1]:
%load_ext autoreload
%autoreload 2

#import viewdat_cno_lib as vdl
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from collections import namedtuple
import geopy.distance
import datetime
import time
import os
import subprocess
import math
import glob
import shutil

# Functions

In [35]:
def read_snr_tsv(fname):
    dtypes = {
            '%  Week': int,
            'Time': float,
            'offset': float,
            'RAIM': int,
            'SV': int,
            'FDMA': int,
            'SVChan': int,
            'SVType': int,
            'SVFlags': int,
            'Az': float,
            'El': float,
            'Freq': int,
            'Track': int,
            'Phase': float,
            'Range': float,
            'Doppler': float,
            'CNo': float,
            'Count': int,
            'Flags': int,
            'Antenna': int,
            'TrackState': int,
            'ScintFlags': int,
            }
    
    line_no = 0
    with open(fname) as file:
        for line in file:
            if '%  Week ' in line:
                break
            line_no += 1

    df = pd.read_csv(fname, delimiter='\t', header=line_no, dtype=dtypes)
    df.rename(columns=lambda x: x.strip(), inplace=True)  # drop whitespace
    df.rename(columns={'%  Week': 'Week'}, inplace=True)
    df.rename(columns={'TRACK': 'Track'}, inplace=True)
    
    d_sv_type = {
        0: 'GPS',
        1: 'SBAS',
        2: 'GLONASS',
        3: 'Galileo',
        4: 'QZSS',
        5: 'BeiDou',
        6: 'OmniStar',
        7: 'BeiDou',
        8: 'XPS',
        9: 'IRNSS',
        10: 'BeiDou',
       }
    # Use the d_sv_type dictionary to replace values in the SV_TYPE column
    df = df.replace({"SVType": d_sv_type})
    d_freq_type = {
        0:  'L1',
        1:  'L2',
        2:  'L5/E5A',
        3:  'E5B/B2',
        4:  'E5A+B',
        5:  'E6',
        6:  'B1',
        7:  'B3',
        8:  'E1',
        9:  'G3',
        10: 'XPS',
        11: 'S1'
        }
    # Use the d_freq_type dictionary to replace values in the Freq column
    df = df.replace({"Freq": d_freq_type})
    
    #if antenna is not None and 'Antenna' in df.columns:
    #    df = df[df.Antenna == antenna]
    
    # Force data types for optimal processesing speed
    # df = df.astype(REC35_DTYPE_DICT)
    return df

In [44]:
def snr_counts(df, name):
    ant0_count = df.query('Antenna==0').shape[0]
    ant1_count = df.query('Antenna==1').shape[0]

    print(f'Total: {df.shape[0]:,}')
    print(f'Ant 0: {ant0_count:,} = {ant0_count/df.shape[0]*100:.2f}%')
    print(f'Ant 1: {ant1_count:,} = {ant1_count/df.shape[0]*100:.2f}%')
    print(f'Delta: {ant0_count - ant1_count:,}')

    d = {
        'name': name,
        'total': df_judo.shape[0],
        'ant0': ant0_count,
        'ant1': ant1_count,
        'delta': ant0_count - ant1_count,
    }
    return d

#d = snr_counts(df_judo, '0715-0717/6303c55359.tsv')

# Process Files

In [45]:
# viewdat -i -d35:19 -mb -h 0715-0717/6303C55359/6303*.T04 -o0715-0717/6303C55359.tsv
# and similar to generate the other other .tsv files 
df_judo = read_snr_tsv('0715-0717/6303c55359.tsv')

In [42]:
fname_list = [
    '0715-0717/bx2geo.tsv',
    '0715-0717/6303c55359.tsv',
    '0715-0717/6348c01926.tsv',

    '0717-0722/bxgeo.tsv',
    '0717-0722/6303c55359.tsv',
    '0717-0722/6348c01926.tsv',
]
records = []
for fname in fname_list:
    print(f'Processing: {fname}')
    df = read_snr_tsv(fname)
    #display(df)
    record = snr_counts(df, fname)
    records.append(record)

df = pd.DataFrame(records)

Processing: 0715-0717/bx2geo.tsv
Total: 406,706
Ant 0: 406,706 = 100.00%
Ant 1: 0 = 0.00%
Delta: 406,706
Processing: 0715-0717/6303c55359.tsv
Total: 811,330
Ant 0: 416,465 = 51.33%
Ant 1: 394,865 = 48.67%
Delta: 21,600
Processing: 0715-0717/6348c01926.tsv
Total: 767,478
Ant 0: 394,539 = 51.41%
Ant 1: 372,939 = 48.59%
Delta: 21,600
Processing: 0717-0722/bxgeo.tsv
Total: 435,244
Ant 0: 435,244 = 100.00%
Ant 1: 0 = 0.00%
Delta: 435,244
Processing: 0717-0722/6303c55359.tsv
Total: 801,730
Ant 0: 411,678 = 51.35%
Ant 1: 390,052 = 48.65%
Delta: 21,626
Processing: 0717-0722/6348c01926.tsv
Total: 757,922
Ant 0: 389,763 = 51.43%
Ant 1: 368,159 = 48.57%
Delta: 21,604


In [43]:
display(df)

name   total    ant0    ant1   delta
0      0715-0717/bx2geo.tsv  811330  406706       0  406706
1  0715-0717/6303c55359.tsv  811330  416465  394865   21600
2  0715-0717/6348c01926.tsv  811330  394539  372939   21600
3       0717-0722/bxgeo.tsv  811330  435244       0  435244
4  0717-0722/6303c55359.tsv  811330  411678  390052   21626
5  0717-0722/6348c01926.tsv  811330  389763  368159   21604